In [1]:
from google.cloud import bigquery
client_bq = bigquery.Client.from_service_account_json("./credentials.json", project='charged-dialect-824')

# Loading data from BQ

In [2]:
def load_bq_data(_sql):
    _df = client_bq.query(_sql).to_dataframe()
    return _df

In [3]:
sql = """
SELECT *
FROM RicardoInterview.product_detection_training_data
"""

df_load = load_bq_data(sql)
len(df_load)
df_load.head()

articleId                                     title  \
0 -3393892867263864215               Gone Is Gone - Echolocation   
1 -2831118468819601923  Ekseption-The Lost Last Concert Tapes...   
2  6835807414137785977          PORTISHEAD CD-Sammlung 3 CDs #16   
3 -4912458353746230865              Primeon CD-R Rohlinge (bunt)   
4  1496864991301777371                  Adonia - Zmittst im Füür   

                                            subtitle productType  
0                        Gone Is Gone - Echolocation          cd  
1              The Lost Last Concert Tapes (Box-Set)          cd  
2  Kollektion für Fans der Trip-Hop-Pioniere aus ...          cd  
3                           39 Stück auf der Spindel          cd  
4                   Markus Hottiger / Markus Heusser          cd

In [ ]:
df = df_load
print(len(df))

# Some Sample

In [174]:
df[['title','subtitle','productType']].fillna('').sample(20)

title  \
14608  Sichler Haushaltsgeräte Kompakter Dampfb   
5537                             Kleiderschrank   
3514              Motorrad Handschuhe Touratech   
34543                             Kinderboxsack   
26513       38/40, Wetlook Leggings von YU & ME   
34539                             Boxsack Feder   
23891            D+L Apex 55437 30kW Heizkanone   
8587        Golftrolley Big Max Autofold+ weiss   
35224                              Bilderrahmen   
7538                 STING HERREN  SONNENBRILLE   
18673                  Würfel-Design E27  Lampe   
5931    Winterjacke Damen -Parajumpers XS Damen   
32966                             Kerzenständer   
8747          Schaukelstuhl Bugholz verstellbar   
22603                Seilwinde mit Elektromotor   
5430                      MESSERBÄNKLI BACCARAT   
25547      RP Gummimatten Peugeot 4008 ab 2012-   
8578        eTrolley OffMeTrolley ohne Batterie   
26361          Hotpot Badefass Badezuber Hottub   
24018                            Zara Man Jacke   

                                                subtitle    productType  
14608                          Schlagen Sie jetzt zu....  steam_cleaner  
5537   Profitieren Sie jetzt von besonderen LIPO Tief...         carton  
3514                        Touratech Guardo Desert Gr.7          glove  
34543                                                      punching_bag  
26513                                                           leggins  
34539                                                      punching_bag  
23891                                                            heater  
8587                     Top zustand, 1 Saison gebraucht        trolley  
35224                                                     picture_frame  
7538   Metall verchromt, Gläser grau degradé 100% UV-...        glasses  
18673                                                              lamp  
5931                                              Bomber         jacket  
32966                                                       candlestick  
8747           Schaukelstuhl Bugholz verstellbar Schwarz       armchair  
22603                                                             winch  
5430                               MESSERBÄNKLI BACCARAT         carafe  
25547                                                           car_mat  
8578                   Elektro Trolley, Caddy, Golfwagen        trolley  
26361                                                           jacuzzi  
24018                                                            jacket

# Check languages and store to file

In [ ]:
from langdetect import detect
tqdm.pandas()

def get_lang(s):
    try:
        language = detect(s)
    except:
        language = "error"
        print(f"ERROR: {s}")
    return language

df['lang'] = (df['title'].fillna('').astype(str) + df['subtitle'].fillna('').astype(str)).progress_apply(lambda x: get_lang(x))

# store to file as backup
df.to_csv('../data/articles.csv',index=False)

# Load data from file

In [1]:
import pandas as pd 
import numpy as np
import plotly.express as px

df = pd.read_csv('../data/articles.csv')
print(len(df))

37567


In [9]:
# Plot language distribution
fig = px.bar(df['lang'].value_counts(),height=600,width=1000)
fig.update_layout(
    autosize=False,
    width=1000,
    height=600,
    font=dict(
        size=20,
    ),
    showlegend=False,
    xaxis_title="language",
    yaxis_title="count"
)
fig.show()

In [183]:
# Export for huggingface AutoNLP to obtain a baseline
df_de = df[ df['lang'] == 'de' ]
df_de[['text','productType']].to_csv('../data/articles_de_hf.csv',index=False)

# Read precomputed embeddings

In [12]:
# To compute embeddings, the methods in app/embeddings.py are used

# bert embeddings
vecs_bert = np.load('../data/embeddings_bert.npy')
print(vecs_bert.shape)

# Sparse embeddings
import scipy.sparse as sp
vecs_sp = sp.load_npz('../data/embeddings_sparse.npz')
print(vecs_sp.shape)

# Combine both embeddings
vecs = sp.hstack([sp.csr_matrix(vecs_bert),vecs_sp])
print(vecs.shape)


(37567, 768)
(37567, 8884)
(37567, 9652)


## Plot dense embedding

In [315]:
# Project to 2 dims with TSNE
from sklearn.manifold import TSNE
tsne = TSNE(n_components=2, random_state=42)
vecs_ = tsne.fit_transform(vecs_bert)

In [319]:
df_plot = pd.DataFrame(vecs_)
df_plot['title'] = df['title']
df_plot['subtitle'] = df['subtitle']
df_plot['productType'] = df['productType']
df_plot['lang'] = df['lang']

In [320]:
fig = px.scatter(df_plot, x=0,y=1,color='productType',hover_data=['title','subtitle'],width=1200,height=800)
fig.update_layout(font_size=15,legend=dict(title=""))
fig.update_yaxes(title='', showticklabels=False)
fig.update_xaxes(title='', showticklabels=False)

# Train linear model

In [31]:
from sklearn.linear_model import LogisticRegression, SGDClassifier
from sklearn.model_selection import cross_val_predict
from sklearn.metrics import accuracy_score, f1_score

# Exclude only french since other languages are not correctly classified
df_de = df[ df['lang'] != 'fr' ].copy()

# Model input
X = vecs[df_de.index,:]
Y = df_de['productType']

#mod = LogisticRegression(class_weight='balanced',multi_class='multinomial',solver='lbfgs',max_iter=10,verbose=10)#,C=100)
mod = SGDClassifier(validation_fraction=0.2,early_stopping=True,verbose=0,max_iter=10,n_jobs=6,loss='log_loss') #due to speed, restrict to SGD

Y_pred = cross_val_predict(mod, X, Y, cv=30)
print('accuracy:', accuracy_score(Y,Y_pred).round(3))
print('f1:', f1_score(Y,Y_pred,average='weighted').round(3))

In [ ]:
# Compare to without cross-validation
mod.fit(X,Y)
Y_pred_ = mod.predict(X)
print('accuracy:', accuracy_score(Y,Y_pred_).round(3))
print('f1:', f1_score(Y,Y_pred_,average='weighted').round(3))

accuracy: 0.918
f1: 0.918


# Confusion matrix

In [24]:
from sklearn.metrics import confusion_matrix

cm = confusion_matrix(Y, Y_pred)
df_cm = pd.DataFrame(cm)

df_cm = pd.DataFrame(cm)
df_cm.index = mod.classes_
df_cm.columns = mod.classes_

diagonal_values = np.diag(df_cm)
indices = np.argsort(diagonal_values)

df_cm = df_cm.iloc[indices, :]
df_cm = df_cm[df_cm.index]

In [25]:
import plotly.graph_objects as go

fig = go.Figure(data=go.Heatmap(
                   z=df_cm.values,
                   x=df_cm.columns,
                   y=df_cm.index,
                   hoverongaps = False))
fig.update_layout(autosize=False, width=800, height=800)
fig.show()

# Write model to app directory

In [30]:
import pickle
with open('../app/model.pkl', 'wb') as file:
    pickle.dump(mod, file)
